In [1]:
import os
os.environ['CUDA_VISIBLE_DEVICES']='7'

In [2]:
from transformers import AutoTokenizer
import re
import numpy as np
from random import Random
import torch
import pandas as pd
import spacy
import random
from datasets import load_dataset
from transformers import (
    AutoModelForTokenClassification,
    AutoTokenizer,
    DataCollatorForTokenClassification,
    TrainingArguments,
    Trainer,
    set_seed)
import numpy as np
import datasets
from collections import defaultdict
from datasets import load_metric

2023-02-26 02:35:07.275938: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-02-26 02:35:07.472394: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2023-02-26 02:35:07.472434: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
2023-02-26 02:35:07.503598: E tensorflow/stream_executor/cuda/cuda_blas.cc:2981] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2023-02-26 02:35:08.603575: W tensorflow/stream_executor/platform/de

In [3]:
# !pip install seqeval

In [4]:
per_device_train_batch_size = 16
per_device_eval_batch_size = 32
num_train_epochs = 5
weight_decay = 0.1
warmup_ratio = 0.1
learning_rate = 5e-5
load_best_model_at_end = True
output_dir = "../akoksal/earthquake_ner_models/"
old_data_path = "annotated_address_dataset_07022023_766train_192test/"
data_path = "deprem-private/ner_v12"
cache_dir = "../akoksal/hf_cache"
saved_models_path = "../akoksal/earthquake_ner_models/"
device = "cuda"
seed = 42
model_names = ["dbmdz/bert-base-turkish-cased",
              "dbmdz/electra-base-turkish-mc4-cased-discriminator",
              "dbmdz/bert-base-turkish-128k-cased",
              "dbmdz/convbert-base-turkish-cased",
              "bert-base-multilingual-cased",
              "xlm-roberta-base"]
model_name = model_names[2]

In [5]:
model_name

'dbmdz/bert-base-turkish-128k-cased'

In [6]:
set_seed(seed)

In [7]:
id2label = {
    0: "O",
    1: "B-bina",
    2: "I-bina",
    3: "B-bulvar",
    4: "I-bulvar",
    5: "B-cadde",
    6: "I-cadde",
    7: "B-diskapino",
    8: "I-diskapino",
    9: "B-ilce",
    10: "I-ilce",
    11: "B-isim",
    12: "I-isim",
    13: "B-mahalle",
    14: "I-mahalle",
    15: "B-sehir",
    16: "I-sehir",
    17: "B-site",
    18: "I-site",
    19: "B-sokak",
    20: "I-sokak",
    21: "B-soyisim",
    22: "I-soyisim",
    23: "B-telefonno",
    24: "I-telefonno",
}

label2id = {label: idx for idx, label in id2label.items()}
label_names = list(label2id.keys())

In [8]:
# from huggingface_hub import login
# login()

In [9]:
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForTokenClassification.from_pretrained(model_name,
                                                        num_labels=len(label_names),
                                                        id2label=id2label,
                                                        cache_dir=cache_dir).to(device)

Some weights of the model checkpoint at dbmdz/bert-base-turkish-128k-cased were not used when initializing BertForTokenClassification: ['cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias']
- This IS expected if you are initializing BertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForTokenClassification were not ini

In [10]:
raw_dataset = datasets.load_dataset("deprem-private/ner_v12", use_auth_token=True)

new_dataset_json = {}
for split in ["train", "validation", "test"]:
    ids = []
    sentences = []
    labels = []
    ids = []
    cur_idx = 0
    unique_labels = set()
    temp_sent = []
    temp_labels = []
    for word in raw_dataset[split]["text"]:
        
        if word!="":
            temp_sent.append((word.split()[0]))
            temp_labels.append(label2id[(word.split()[1])])
        else:
            sentences.append(temp_sent)
            labels.append(temp_labels)
            ids.append(cur_idx)
            cur_idx+=1
            temp_sent = []
            temp_labels = []
    new_dataset_json[split] = {"tokens":sentences, "ner_tags":labels, "ids":ids}

dataset = datasets.DatasetDict()
# using your `Dict` object
for k,v in new_dataset_json.items():
    dataset[k] = datasets.Dataset.from_dict(v)

Using custom data configuration deprem-private--ner_v12-e2f61c5a18a7a738
Found cached dataset text (/mounts/Users/cisintern/akoksal/.cache/huggingface/datasets/deprem-private___text/deprem-private--ner_v12-e2f61c5a18a7a738/0.0.0/cb1e9bd71a82ad27976be3b12b407850fe2837d80c22c5e03a28949843a8ace2)


  0%|          | 0/3 [00:00<?, ?it/s]

In [11]:
# dataset = datasets.load_from_disk(old_data_path)
def tokenize_and_align_labels(examples):
    tokenized_inputs = tokenizer(examples["tokens"], truncation=True, is_split_into_words=True)

    labels = []
    for i, label in enumerate(examples[f"ner_tags"]):
        word_ids = tokenized_inputs.word_ids(batch_index=i)  # Map tokens to their respective word.
        previous_word_idx = None
        label_ids = []
        for word_idx in word_ids:  # Set the special tokens to -100.
            if word_idx is None:
                label_ids.append(-100)
            elif word_idx != previous_word_idx:  # Only label the first token of a given word.
                label_ids.append(label[word_idx])
            else:
                label_ids.append(-100)
            previous_word_idx = word_idx
        labels.append(label_ids)

    tokenized_inputs["labels"] = labels
    return tokenized_inputs

tokenized_dataset = dataset.map(tokenize_and_align_labels, batched=True)

  0%|          | 0/1 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

In [12]:
data_collator = DataCollatorForTokenClassification(tokenizer)

In [13]:
metric = load_metric("seqeval")
def compute_metrics(p):
    predictions, labels = p
    predictions = np.argmax(predictions, axis=2)

    # Remove ignored index (special tokens)
    true_predictions = [
        [label_names[p] for (p, l) in zip(prediction, label) if l != -100]
        for prediction, label in zip(predictions, labels)
    ]
    true_labels = [
        [label_names[l] for (p, l) in zip(prediction, label) if l != -100]
        for prediction, label in zip(predictions, labels)
    ]

    results = metric.compute(predictions=true_predictions, references=true_labels)
    flattened_results = {
        "overall_precision": results["overall_precision"],
        "overall_recall": results["overall_recall"],
        "overall_f1": results["overall_f1"],
        "overall_accuracy": results["overall_accuracy"],
    }
    for k in results.keys():
        if(k not in flattened_results.keys()):
            flattened_results[k+"_f1"]=results[k]["f1"]
            flattened_results[k+"_recall"]=results[k]["recall"]
            flattened_results[k+"_precision"]=results[k]["precision"]
            flattened_results[k+"_support"]=results[k]["number"]

    return flattened_results

/tmp/ipykernel_2652487/885599324.py:1: FutureWarning: load_metric is deprecated and will be removed in the next major version of datasets. Use 'evaluate.load' instead, from the new library 🤗 Evaluate: https://huggingface.co/docs/evaluate
  metric = load_metric("seqeval")


In [14]:
training_args = TrainingArguments(
    output_dir=saved_models_path,
    evaluation_strategy="epoch",
    learning_rate=learning_rate,
    per_device_train_batch_size=per_device_train_batch_size,
    per_device_eval_batch_size=per_device_eval_batch_size,
    num_train_epochs=num_train_epochs,
    warmup_ratio=warmup_ratio,
    weight_decay=weight_decay,
    run_name = "turkish_ner",
    save_strategy='epoch',
    logging_strategy="epoch",
    save_total_limit=3,
    load_best_model_at_end=load_best_model_at_end,
    
)
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_dataset["train"],
    eval_dataset=tokenized_dataset["validation"],
    data_collator=data_collator,
    tokenizer=tokenizer,
    compute_metrics=compute_metrics
)

In [15]:
trainer.train()

The following columns in the training set don't have a corresponding argument in `BertForTokenClassification.forward` and have been ignored: tokens, ids, ner_tags. If tokens, ids, ner_tags are not expected by `BertForTokenClassification.forward`,  you can safely ignore this message.
/mounts/work/akoksal/anaconda3/envs/lmbias/lib/python3.9/site-packages/transformers/optimization.py:306: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
***** Running training *****
  Num examples = 799
  Num Epochs = 5
  Instantaneous batch size per device = 16
  Total train batch size (w. parallel, distributed & accumulation) = 16
  Gradient Accumulation steps = 1
  Total optimization steps = 250
  Number of trainable parameters = 183773977
You're using a BertTokenizerFast tokenizer. Please note that with a fast tokenizer

The following columns in the evaluation set don't have a corresponding argument in `BertForTokenClassification.forward` and have been ignored: tokens, ids, ner_tags. If tokens, ids, ner_tags are not expected by `BertForTokenClassification.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 58
  Batch size = 32
/mounts/work/akoksal/anaconda3/envs/lmbias/lib/python3.9/site-packages/seqeval/metrics/v1.py:57: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
Saving model checkpoint to /mounts/work/akoksal/earthquake_ner_models/checkpoint-50
Configuration saved in /mounts/work/akoksal/earthquake_ner_models/checkpoint-50/config.json
Model weights saved in /mounts/work/akoksal/earthquake_ner_models/checkpoint-50/pytorch_model.bin
tokenizer config file saved in /mounts/work

TrainOutput(global_step=250, training_loss=0.3963502960205078, metrics={'train_runtime': 73.0701, 'train_samples_per_second': 54.674, 'train_steps_per_second': 3.421, 'total_flos': 129863927953500.0, 'train_loss': 0.3963502960205078, 'epoch': 5.0})

In [16]:
results = trainer.evaluate(tokenized_dataset["test"])

The following columns in the evaluation set don't have a corresponding argument in `BertForTokenClassification.forward` and have been ignored: tokens, ids, ner_tags. If tokens, ids, ner_tags are not expected by `BertForTokenClassification.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 129
  Batch size = 32


In [24]:
results

{'eval_loss': 0.24822480976581573,
 'eval_overall_precision': 0.8442211055276382,
 'eval_overall_recall': 0.877742946708464,
 'eval_overall_f1': 0.860655737704918,
 'eval_overall_accuracy': 0.9401853411962932,
 'eval_bina_f1': 0.7000000000000001,
 'eval_bina_recall': 0.7424242424242424,
 'eval_bina_precision': 0.6621621621621622,
 'eval_bina_support': 66,
 'eval_bulvar_f1': 0.9230769230769231,
 'eval_bulvar_recall': 0.9230769230769231,
 'eval_bulvar_precision': 0.9230769230769231,
 'eval_bulvar_support': 13,
 'eval_cadde_f1': 0.8067226890756302,
 'eval_cadde_recall': 0.8421052631578947,
 'eval_cadde_precision': 0.7741935483870968,
 'eval_cadde_support': 57,
 'eval_diskapino_f1': 0.7083333333333334,
 'eval_diskapino_recall': 0.7285714285714285,
 'eval_diskapino_precision': 0.6891891891891891,
 'eval_diskapino_support': 70,
 'eval_ilce_f1': 0.9218106995884773,
 'eval_ilce_recall': 0.9572649572649573,
 'eval_ilce_precision': 0.8888888888888888,
 'eval_ilce_support': 117,
 'eval_isim_f1': 

In [18]:
structured_results = defaultdict(dict)
structured_results["overall"]["support"]=0
for x, y in results.items():
    if len(x.split("_"))==3:
        structured_results[x.split("_")[1]][x.split("_")[2]] = y
        if x.split("_")[2]=="support":
            structured_results["overall"]["support"]+=y
results_pd = pd.DataFrame(structured_results).T
results_pd.support = results_pd.support.astype(int)
results_pd.round(2)

support  precision  recall    f1  accuracy
overall        957       0.84    0.88  0.86      0.94
bina            66       0.66    0.74  0.70       NaN
bulvar          13       0.92    0.92  0.92       NaN
cadde           57       0.77    0.84  0.81       NaN
diskapino       70       0.69    0.73  0.71       NaN
ilce           117       0.89    0.96  0.92       NaN
isim           113       0.86    0.90  0.88       NaN
mahalle        120       0.77    0.82  0.79       NaN
sehir          146       0.98    0.97  0.97       NaN
site            18       0.79    0.61  0.69       NaN
sokak           62       0.72    0.74  0.73       NaN
soyisim         98       0.94    0.95  0.94       NaN
telefonno       77       0.99    1.00  0.99       NaN

## Predictions

In [19]:
from transformers import pipeline
nlp = pipeline("ner", model=model.to(device), tokenizer=tokenizer, aggregation_strategy="first", device=0 if device=="cuda" else -1)

In [20]:
# Source: https://www.thepythoncode.com/article/named-entity-recognition-using-transformers-and-spacy
def get_entities_html(text, ner_result, title=None):
    """Visualize NER with the help of SpaCy"""
    ents = []
    for ent in ner_result:
        e = {}
        # add the start and end positions of the entity
        e["start"] = ent["start"]
        e["end"] = ent["end"]
        # add the score if you want in the label
        # e["label"] = f"{ent["entity"]}-{ent['score']:.2f}"
        e["label"] = ent["entity_group"]
        if ents and -1 <= ent["start"] - ents[-1]["end"] <= 1 and ents[-1]["label"] == e["label"]:
            # if the current entity is shared with previous entity
            # simply extend the entity end position instead of adding a new one
            ents[-1]["end"] = e["end"]
            continue
        ents.append(e)
      # construct data required for displacy.render() method
    render_data = [
    {
      "text": text,
      "ents": ents,
      "title": title,
    }
    ]
    spacy.displacy.render(render_data, style="ent", manual=True, jupyter=True)

In [21]:
sentence = """Lütfen yardım Akevler mahallesi Rüzgar sokak Tuncay apartmanı zemin kat Antakya akrabalarım göçük altında #hatay #Afad"""

get_entities_html(sentence, nlp(sentence))

In [22]:
sentence = " ".join(dataset["train"][433]["tokens"])
get_entities_html(sentence, nlp(sentence))